In [5]:
import statsmodels.api as sm 
import umap
from io import StringIO
from os.path import join
import pandas as pd
import xlsxwriter
import openpyxl
import os
import numpy as np
import itertools
import itertools as it
import kaleido
from pandas import Series, ExcelWriter
import scipy.io as sio
import plotly.graph_objects as go
import plotly.io as pio
import plotly.express as px
import seaborn as sns
from IPython.display import display, HTML
from fpdf import FPDF
import scanpy as sc 
from anndata import AnnData
import csv
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib.lines import Line2D  # for legend handle

In [8]:
import sys  
sys.path.insert(0, 'C:/Users/morts/Documents/TAU/Manifold_Project/code/my_packages')
import dimen_reduc
import meta_ord
import paga_res
import sliding_window
import statistic

#### Variables

In [1]:
top_path = 'C:/Users/morts/Documents/TAU/Manifold_Project/Data/SPECIFIC_PAPERS/'

db_path1 = top_path + 'Ravel_et_al.2013/Ravel2013_MT_16052023.xlsx'
db_path2 = top_path + 'Carter_et_al.2022/Carter2022_MT_16052023.xlsx'
db_path3 = top_path + 'Ravel_et_al.2011/Ravel2011_MT_16052023.xlsx'
db_path4 = top_path + 'Serrano_et_al.2019/noDuplicatedID/Serrano_MT_16052023.xlsx'
db_path5 = top_path + 'Srinivasan_et_al.2012/Srinivasan2012_MT_25012023_BVstatus.xlsx'

db_lst = [db_path1, db_path2, db_path3, db_path4, db_path5]
sra_lst = [False, False, False, False, False, False]

date = '25062023'

sheet_abun = 'abundance'
sheet_meta = 'meta'

#### Load data

In [2]:
db_names = ['temp', 'carter', 'cros_II', 'cros_I', 'srin']

In [3]:
def remove_rare_species(df, prevalence_cutoff = 0.1, avg_abundance_cutoff = 0.005):
    filt_df = df.copy()
    n_samples = df.shape[0]
    n_taxa_before_filter = df.shape[1]
    
    # Prevalence calculations (number of non-zero values per feature)
    frequencies = (df > 0).sum(axis = 0) / n_samples
    filt_df = filt_df.loc[:,frequencies > prevalence_cutoff]
    
    # Average abundance calculations
    avg_abundances = df.sum(axis = 0) / n_samples
    filt_df = filt_df.loc[:, avg_abundances > avg_abundance_cutoff]
    
    # Order
    s = filt_df.sum()
    filt_df = filt_df[s.sort_values(ascending = False).index]
    
    return filt_df

In [9]:
df_lst = []
meta_lst = []
for i, file in enumerate(db_lst):
    df = pd.read_excel(file, sheet_name = sheet_abun, index_col = 0)
    meta = pd.read_excel(file, sheet_name = sheet_meta, index_col = 0)
    
    ## meta order
    if not 'db' in meta.columns:
        meta['db'] = db_names[i]
    
    meta = meta_ord.get_shannon(df, meta)
    
    if db_names[i] == 'carter':
        meta['ph'] = np.where(meta['ph'] >= 1, 5.5, 0)
    
    ## df abundance order
    if df.shape[0] != meta.shape[0]:
        df = df.loc[meta.index]
    
#     filt_df = remove_rare_species(df)
#     print(df.shape)
#     print(filt_df.shape)
    
    df_lst.append(df)
    meta_lst.append(meta)

In [10]:
for i, df in enumerate(df_lst):
    print(df.shape)
    print(meta_lst[i].shape)

(3597, 296)
(3597, 23)
(495, 137)
(495, 13)
(385, 54)
(385, 10)
(3879, 278)
(3879, 5)
(185, 33)
(185, 17)


In [12]:
len(df_lst[4].columns & df_lst[0].columns)

C:\Users\morts\miniconda3\envs\py37\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Index.__and__ operating as a set operation is deprecated, in the future this will be a logical operation matching Series.__and__.  Use index.intersection(other) instead
  """Entry point for launching an IPython kernel.


32

In [13]:
for i, df in enumerate(df_lst):
    print('first df shape: ', len(df.columns))
    print('serrano df shape: ', len(df_lst[3].columns))
#     print(len(df.columns & df_lst[i + 1].columns))
    print(len(df.columns & df_lst[3].columns))
    print([col for col in df_lst[3].columns if col not in df.columns & df_lst[3].columns])
    print([col for col in df.columns if col not in df.columns & df_lst[3].columns])

first df shape:  296
serrano df shape:  278
165
['Lactobacillus_animalis', 'Lactobacillus_colini', 'Lactobacillus_equicursoris', 'Lactobacillus_frumenti', 'Lactobacillus_halophilus', 'Lactobacillus_mucosae', 'Lactobacillus_paracasei', 'Prevotella_intermedia', 'Prevotella_nanceiensis', 'Prevotella_nigrescens', 'Prevotella_oris', 'Prevotella_veroralis', 'Prevotellamassilia_timonensis', 'c_Bacteroidia', 'f_Comamonadaceae', 'f_Crocinitomicaceae', 'f_Erysipelatoclostridiaceae', 'f_Methylopilaceae', 'f_Mitochondria', 'f_Paracaedibacteraceae', 'f_Puniceicoccaceae', 'f_Solirubrobacteraceae', 'f_Sphingomonadaceae', 'f_env.OPS 17', 'g_Aeriscardovia', 'g_Afipia', 'g_Agathobacter', 'g_Agromyces', 'g_Allorhizobium-Neorhizobium-Pararhizobium-Rhizobium', 'g_Anoxybacillus', 'g_Aquabacterium', 'g_Arthrobacter', 'g_Atopobacter', 'g_Atopostipes', 'g_Blastomonas', 'g_Bosea', 'g_Bradyrhizobium', 'g_Brevundimonas', 'g_Brochothrix', 'g_Burkholderia-Caballeronia-Paraburkholderia', 'g_Butyricicoccus', 'g_CAG-3

C:\Users\morts\miniconda3\envs\py37\lib\site-packages\ipykernel_launcher.py:5: FutureWarning: Index.__and__ operating as a set operation is deprecated, in the future this will be a logical operation matching Series.__and__.  Use index.intersection(other) instead
  """
C:\Users\morts\miniconda3\envs\py37\lib\site-packages\ipykernel_launcher.py:6: FutureWarning: Index.__and__ operating as a set operation is deprecated, in the future this will be a logical operation matching Series.__and__.  Use index.intersection(other) instead
  
C:\Users\morts\miniconda3\envs\py37\lib\site-packages\ipykernel_launcher.py:7: FutureWarning: Index.__and__ operating as a set operation is deprecated, in the future this will be a logical operation matching Series.__and__.  Use index.intersection(other) instead
  import sys


['BVAB2', 'BVAB3', 'Lactobacillus_antri', 'Lactobacillus_apodemi', 'Lactobacillus_johnsonii', 'Lactobacillus_kefiranofaciens', 'Prevotella_baroniae', 'Prevotella_brevis', 'Prevotella_multiformis', 'c_Betaproteobacteria', 'f_Bacteroidales_S24-7_group', 'f_Coriobacteriaceae', 'f_Mycoplasmataceae', 'g_Albidiferax', 'g_Candidatus', 'g_Escherichia/Shigella', 'g_Lachnoanaerobaculum', 'g_Limnobacter', 'g_Methylobacterium', 'g_Methyloversatilis', 'g_Perlucidibaca', 'g_Pseudobutyrivibrio', 'g_Raoultella', 'g_Rhodoferax', 'g_Rikenellaceae', 'g_Ruminococcaceae', 'g_Senegalimassilia', 'g_Succinivibrio', 'o_Burkholderiales', 'o_Clostridiales', 'o_Lactobacillales', 'o_Micrococcales', 'o_Sphingomonadales', 'p_Proteobacteria', 'p_Saccharibacteria']
first df shape:  54
serrano df shape:  278
50
['Atopobium_deltae', 'Atopobium_minutum', 'Lactobacillus_animalis', 'Lactobacillus_coleohominis', 'Lactobacillus_colini', 'Lactobacillus_delbrueckii', 'Lactobacillus_equicursoris', 'Lactobacillus_fermentum', 'La

#### Merge

In [14]:
all_df = pd.concat(df_lst)
all_df.fillna(0, inplace = True)
all_df.shape

(8541, 425)

In [15]:
all_meta = pd.concat(meta_lst)
all_meta.shape

(8541, 31)

#### Order meta columns

In [16]:
all_meta['BV_status'] = np.select([all_meta['ABV'] == 1, all_meta['SBV'] == 1], ['ABV', 'SBV'], default = all_meta['BV_status'])
all_meta['BV_bin'] = np.where((all_meta['BV_status'] == 'ABV') | (all_meta['BV_status'] == 'SBV'), 1, 0)

all_meta['subjectID'] = all_meta['subjectID'].fillna('VCU')
# all_meta['sampleID'] = all_meta['run']
all_meta['sampleID'].fillna(all_meta.index.to_series(), inplace = True)
# all_meta.drop(['run', 'community', 'symptoms_sum', 'others_sum', 'amsel_sum'], axis = 1, inplace = True)

In [17]:
all_meta.groupby('db')['subjectID'].count()

db
carter         495
cros_I        3879
cros_II        385
srin           185
temp_hiseq    2024
temp_pyro     1573
Name: subjectID, dtype: int64

In [18]:
print(all_meta.BV_status.unique())
print(all_meta.BV_bin.unique())

[nan 'SBV' 'ABV' 'HC']
[0 1]


In [19]:
dict_res = {'abundance': all_df, 'meta': all_meta}
ps_path = 'C:/Users/morts/Documents/TAU/Manifold_Project/Data/Serrano_Ravel13_Ravel11_Carter22/' + 'all_df_25062023.xlsx'
paga_res.save_excel(ps_path, dict_res)

C:\Users\morts\miniconda3\envs\py37\lib\site-packages\xlsxwriter\workbook.py:338: UserWarning: Calling close() on already closed file.
  warn("Calling close() on already closed file.")


#### Overlook

In [20]:
norm_df = dimen_reduc.get_center(all_df)
pca_array, loadings, variance_ratio, variance = pca_res = dimen_reduc.get_pca_reg(norm_df)
print(pca_array.shape)
pca_df = pd.DataFrame(pca_array[:, :3], columns = ['PC1', 'PC2', 'PC3'], index = all_meta.index)
pca_df = pca_df.merge(all_meta[['db', 'CST', 'subCST']], left_index=True, right_index = True)
px.scatter_3d(pca_df, x = 'PC1', y = 'PC2', z = 'PC3', color = 'db')

(8541, 50)


In [1]:
bc_dist = dimen_reduc.get_bc_dist(all_df)
bc_res = pcoa(bc_dist)
bc = bc_res.samples.iloc[:, :50].to_numpy()
samples, loadings, variance_ratio, variance = dimen_reduc.get_pcoa(bc_dist, all_df, all_df.index)
# print(bc.shape)
# pca_df = pd.DataFrame(samples[:, :3], columns = ['PC1', 'PC2', 'PC3'], index = all_meta.index)
# pca_df = pca_df.merge(all_meta[['db', 'CST', 'subCST']], left_index=True, right_index = True)
# px.scatter_3d(pca_df, x = 'PC1', y = 'PC2', z = 'PC3', color = 'db')

NameError: name 'dimen_reduc' is not defined

In [ ]:
reducer = umap.UMAP(n_neighbors = 20)
embedding = reducer.fit_transform(pca_array)
print(embedding.shape)

In [ ]:
umap_df = pd.DataFrame(embedding, columns = ['fa1', 'fa2'], index = all_meta.index)
umap_df = umap_df.merge(all_meta[['db', 'CST', 'subCST']], left_index = True, right_index = True)
px.scatter(umap_df, x = 'fa1', y = 'fa2', color = 'db')